In [4]:
import numpy as np
import matplotlib.pyplot as plt
import cmocean 
from matplotlib import cm
from matplotlib.colors import ListedColormap, LinearSegmentedColormap
import scipy as sp
import scipy.special 
import seaborn as sns
import scipy.ndimage
from matplotlib.gridspec import GridSpec
%matplotlib inline
from matplotlib import rc
rc('font',**{'family':'sans-serif','sans-serif':['Helvetica'], 'size':20})
rc('text', usetex=True)
rc('text.latex', preamble=r'\usepackage{mathrsfs}')
from matplotlib.gridspec import GridSpec
def remove_ticks(ax):
    for axis in ax:
        axis.set_xticks([])
        axis.set_yticks([])

In [5]:
RC = {'figure.figsize':(10,5),
      'axes.facecolor':'white',
      'axes.edgecolor':' .15',
      'axes.linewidth':' 1.25',
      'axes.grid' : True,
      'grid.color': '.8',
      'font.size' : 15,
     "xtick.major.size": 4, "ytick.major.size": 4}

plt.rcParams.update(RC)
sns.set_palette(sns.color_palette('dark'), n_colors=None, desat=None, color_codes=False)

In [6]:
#Define non-dimensional parameters for the simulation 
Re = 2.478883e+03
Fr = 1.105914e+00
Ri = 1/((Fr/(2*np.pi)))**2
Pr = 7
ch = 50 #input column height

In [7]:
#Define dimensionless functions f and g from equations (2.14) and (2.15) in the manuscript
#These can be easily modified by the user
a = 1
b = 0.8
c = 0.9
d = 0.9 
def f(x):
    return 19/8 + 11/8*np.tanh(a*np.log(x)-b)

def g(x):
    return 2 + np.tanh(c*np.log(x)-d)

In [8]:
#Model name
model = 'pcnn_eps'
dns_data_loc = '../data/DNS_data/Pr7_decaying/'
output_loc = '../data/PCNN_eps/'

In [9]:
t = ['T=0.5','T=1', 'T=2', 'T=4', 'T=6', 'T=7.7']
xdim, zdim = 500, 500
dudz, drdz, eps, empirical_eps, pcnn_eps, pcnn_mean_eps, reb, drtdz, T = [], [],[],[], [],[], [],[],[]
count = 0
for i in range(0,6): #Choose timestep(s) to load here (from the list 't' above)
    T.append(t[i])
    dudz.append(np.load(dns_data_loc+ T[count] +'/dudz.npy').reshape((xdim,zdim)))
    drdz.append(np.load(dns_data_loc+ T[count] + '/drdz.npy').reshape((xdim,zdim)))
    drtdz.append(np.load(dns_data_loc+ T[count] + '/drtdz.npy').reshape((xdim,zdim)))
    eps.append(np.load(dns_data_loc + T[count] + '/eps.npy').reshape((xdim,zdim)))
    empirical_eps.append(f(sp.ndimage.gaussian_filter(dudz[count], sigma=(0,50))*Re/Ri)*dudz[count])
    reb.append(np.mean(eps[count])*Re/Ri)
    pcnn_eps.append(np.load(output_loc+model+'_sample_'+T[count]+'.npy'))
    pcnn_mean_eps.append(np.load(output_loc+model+'_means_'+T[count]+'.npy').reshape((xdim,zdim)))
    count+=1

In [10]:
print(T) #List of selected timesteps to load

['T=0.5', 'T=1', 'T=2', 'T=4', 'T=6', 'T=7.7']


In [15]:
J = 4 #select which timestep to plot for (number corresponding to index from list 'T')
vmin, vmax = -2.5,-0.5
errormin, errormax = 0,2
cmap=cmocean.cm.balance#'coolwarm'
cmap2 = 'gist_gray_r'
fig=plt.figure(figsize=(8,7*8/10))
gs=GridSpec(3,3, width_ratios=[ 1,1, 0.05], wspace=0.15, hspace=0.07, left=0.33, right=1)
gs2 = GridSpec(3,1, wspace=0.1, hspace=0.05, left=0, right=0.28)
rast = True
ax=fig.add_subplot(gs2[1,0], rasterized=rast) 
ax1=fig.add_subplot(gs[0,0], rasterized=rast) 
ax2=fig.add_subplot(gs[0,1], rasterized=rast) 
axcbar1=fig.add_subplot(gs[:,2], rasterized=rast) 
ax3=fig.add_subplot(gs[1,0], rasterized=rast) 
ax4=fig.add_subplot(gs[1,1], rasterized=rast) 
ax5=fig.add_subplot(gs[2,0], rasterized=rast) 
ax6=fig.add_subplot(gs[2,1], rasterized=rast) 
ax.grid(False); ax1.grid(False); ax2.grid(False); ax3.grid(False); ax4.grid(False); ax5.grid(False); ax6.grid(False), axcbar1.grid(False)
zo=-1
ax.pcolormesh(np.log10(eps[J]).T[:350,:350], vmin=vmin,vmax=vmax, cmap=cmap, shading='gouraud', rasterized=rast)
ax.set_title('$\\mathrm{True\ }\\log_{10}\\varepsilon_0$', size=15)
ax1.pcolormesh(pcnn_eps[J].reshape(xdim,zdim).T[:350,:350], vmin=vmin,vmax=vmax, cmap=cmap,shading='gouraud',
              rasterized=rast)
ax1.set_title('$\\mathrm{Predicted\ } \\log_{10}\\varepsilon_0$', size=15)
im2=ax2.pcolormesh(np.abs(pcnn_eps[J].reshape(xdim,zdim).T[:350,:350] -np.log10(eps[J]).reshape(xdim,zdim).T[:350,:350]), shading='gouraud',
                   vmin=errormin,vmax=errormax, cmap=cmap2, rasterized=rast)
ax2.set_title('$\\mathrm{Local \ error} $', size=15)
ax3.pcolormesh(pcnn_mean_eps[J].reshape(xdim,zdim).T[:350,:350], vmin=vmin,vmax=vmax, cmap=cmap, 
              rasterized=rast)
im4=ax4.pcolormesh(np.abs(pcnn_mean_eps[J].reshape(xdim,zdim).T[:350,:350] -np.log10(eps[J]).reshape(xdim,zdim).T[:350,:350]), shading='gouraud',
                   vmin=errormin,vmax=errormax, cmap=cmap2, rasterized=rast)
ax5.pcolormesh(np.log10(empirical_eps[J].reshape(xdim,zdim).T[:350,:350]), vmin=vmin,vmax=vmax, cmap=cmap, shading='gouraud',
               rasterized=rast)
im6=ax6.pcolormesh(np.abs(np.log10(empirical_eps[J].reshape(xdim,zdim).T[:350,:350]) -np.log10(eps[J]).reshape(xdim,zdim).T[:350,:350]),shading='gouraud',
               vmin=errormin,vmax=errormax, cmap=cmap2, rasterized=rast)
cbar = fig.colorbar(im2, cax=axcbar1, 
                    label='$\\log_{10}\\varepsilon_{\\mathrm{pred}} -\\log_{10}\\varepsilon_{\\mathrm{true}} $', 
                    extend='both')
cbar.set_ticks([0,1,2])
remove_ticks([ax, ax1,ax2,ax3,ax4,ax5,ax6])
fig.show()